# Analysis

get the locally saved data

In [1]:
import pickle
import pandas as pd
import os
import sys
import seaborn as sn
import matplotlib.pyplot as plt
from pathlib import Path
import yaml

sys.path.append('/home/joel/projects/driftlon/analysis')
sys.path.append('/home/joel/projects/driftlon')
from correlation import *
from analysis_utils import *

In [2]:
mongo_config = yaml.safe_load(open('/home/joel/projects/driftlon/config.yml', 'r'))['mongodb']
fetcher = DataFetcher(mongo_config['address'], mongo_config['username'], mongo_config['password'])

In [3]:
X = pickle.load(open('../X.pkl', 'rb+'))
Y = pickle.load(open('../Y.pkl', 'rb+'))

In [4]:
len(X), len(Y)

(87303, 87303)

filter for the numeric fields

In [5]:
non_numerical_fields_path = './non_numeric_fields.yaml'

with open(non_numerical_fields_path, 'r') as file_:
    non_numerical_fields = yaml.load(file_.read(),  Loader=yaml.BaseLoader)

In [6]:
all_keys = get_all_keys(X)
common_keys = [x for x in get_common_keys(X) if x not in non_numerical_fields]
data_for_keys = get_data_for_keys(common_keys, X)

In [7]:
all_data = pd.DataFrame(data_for_keys).T.set_axis(common_keys, axis=1)
quant_indices = [common_keys[x[0]] for x in enumerate(all_data.loc[0,:]) if type(x[1])==int] 
data = pd.DataFrame(all_data.loc[:,quant_indices])
converted_data = data.apply(pd.to_numeric)

In [8]:
converted_data.describe()

championId  participantId      spell1Id      spell2Id  stats_assists  \
count  87303.000000   87303.000000  87303.000000  87303.000000   87303.000000   
mean     170.696356       6.254367      6.903886      8.103124       7.710216   
std      199.276353       3.064484      4.055855      4.333837       5.646779   
min        1.000000       1.000000      1.000000      1.000000       0.000000   
25%       42.000000       4.000000      4.000000      4.000000       4.000000   
50%      103.000000       7.000000      4.000000      7.000000       7.000000   
75%      202.000000       9.000000     11.000000     12.000000      11.000000   
max      887.000000      10.000000     21.000000     21.000000      43.000000   

       stats_champLevel  stats_combatPlayerScore  \
count      87303.000000                  87303.0   
mean          13.458724                      0.0   
std            2.646758                      0.0   
min            1.000000                      0.0   
25%           12.000000                      0.0   
50%           14.000000                      0.0   
75%           15.000000                      0.0   
max           18.000000                      0.0   

       stats_damageDealtToObjectives  stats_damageDealtToTurrets  \
count                   87303.000000                87303.000000   
mean                     9015.701728                 2539.271045   
std                      9945.387265                 3028.440469   
min                         0.000000                    0.000000   
25%                      1860.000000                  327.000000   
50%                      5307.000000                 1496.000000   
75%                     12880.000000                 3625.500000   
max                     83654.000000                37941.000000   

       stats_damageSelfMitigated  ...  stats_trueDamageDealtToChampions  \
count               87303.000000  ...                      87303.000000   
mean                15000.532364  ...                       1099.875560   
std                 11955.833238  ...                       1692.174728   
min                     0.000000  ...                          0.000000   
25%                  7077.000000  ...                         76.000000   
50%                 11634.000000  ...                        594.000000   
75%                 19101.000000  ...                       1280.000000   
max                166534.000000  ...                      23906.000000   

       stats_trueDamageTaken  stats_turretKills  stats_unrealKills  \
count           87303.000000       87303.000000            87303.0   
mean             1048.450225           0.955076                0.0   
std              1107.731309           1.285323                0.0   
min                 0.000000           0.000000                0.0   
25%               345.000000           0.000000                0.0   
50%               723.000000           0.000000                0.0   
75%              1368.000000           1.000000                0.0   
max             14942.000000          10.000000                0.0   

       stats_visionScore  stats_visionWardsBoughtInGame  stats_wardsKilled  \
count       87303.000000                   87303.000000       87303.000000   
mean           28.113272                       3.502549           4.036940   
std            20.279080                       3.371286           3.645379   
min             0.000000                       0.000000           0.000000   
25%            15.000000                       1.000000           1.000000   
50%            22.000000                       3.000000           3.000000   
75%            35.000000                       5.000000           6.000000   
max           174.000000                      61.000000          34.000000   

       stats_wardsPlaced        teamId  timeline_participantId  
count       87303.000000  87303.000000            87303.000000  
mean           12.048234    159.058681                6.2

### create correlation matrix

In [ ]:
corr_matrix = converted_data.corr()

In [ ]:
plt.figure(figsize=(30,30))
sn.heatmap(corr_matrix, annot=True, cmap="PiYG", center=0)
plt.savefig('plots/heatmap.png')

In [ ]:
corr_matrix.unstack().dropna().drop_duplicates().sort_values(ascending=False).to_csv('correlations.csv')

### create violin-plots for all numeric fields

In [ ]:
Path('plots/violin').mkdir(parents=True, exist_ok=True)

In [ ]:
N = len(X)

for i in range(len(common_keys)):
    plt.clf();
    column = converted_data.loc[:,common_keys[i]].sample(n=N, ignore_index=True);
    plt.violinplot(column);
    plt.ylabel(common_keys[i]);
    plt.savefig('plots/violin/' + common_keys[i] + '.png');

### create scatter matrix

In [ ]:
converted_data_with_target = converted_data.copy(deep=True)
converted_data_with_target['target'] = [int(y_ > 0) for y_ in Y]

In [ ]:
# plt.figure(figsize=(30,30))
plt.clf();
sn.pairplot(converted_data_with_target.sample(n=100, ignore_index=True))
plt.savefig('plots/pairplot.png')

### correlation with target

In [19]:
X, Y

([{'participantId': 10,
   'teamId': 200,
   'championId': 236,
   'spell1Id': 1,
   'spell2Id': 4,
   'stats_participantId': 10,
   'stats_win': True,
   'stats_item0': 6671,
   'stats_item1': 1038,
   'stats_item2': 3158,
   'stats_item3': 3508,
   'stats_item4': 1055,
   'stats_item5': 0,
   'stats_item6': 3363,
   'stats_kills': 8,
   'stats_deaths': 1,
   'stats_assists': 1,
   'stats_largestKillingSpree': 5,
   'stats_largestMultiKill': 2,
   'stats_killingSprees': 2,
   'stats_longestTimeSpentLiving': 706,
   'stats_doubleKills': 1,
   'stats_tripleKills': 0,
   'stats_quadraKills': 0,
   'stats_pentaKills': 0,
   'stats_unrealKills': 0,
   'stats_totalDamageDealt': 148823,
   'stats_magicDamageDealt': 5191,
   'stats_physicalDamageDealt': 142233,
   'stats_trueDamageDealt': 1398,
   'stats_largestCriticalStrike': 500,
   'stats_totalDamageDealtToChampions': 17281,
   'stats_magicDamageDealtToChampions': 2535,
   'stats_physicalDamageDealtToChampions': 14745,
   'stats_trueDamag